In [1]:
!trtexec

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec
=== Model Options ===
  --uff=<file>                UFF model
  --onnx=<file>               ONNX model
  --model=<file>              Caffe model (default = no model, random weights used)
  --deploy=<file>             Caffe prototxt file
  --output=<name>[,<name>]*   Output names (it can be specified multiple times); at least one output is required for UFF and Caffe
  --uffInput=<name>,X,Y,Z     Input blob name and its dimensions (X,Y,Z=C,H,W), it can be specified multiple times; at least one is required for UFF models
  --uffNHWC                   Set if inputs are in the NHWC layout instead of NCHW (use X,Y,Z=H,W,C order in --uffInput)

=== Build Options ===
  --maxBatch                  Set max batch size and build an implicit batch engine (default = same size as --batch)
                              This option should not be used when the input model is ONNX or when dynamic shapes are provided.
  --minShapes=spec            B

In [2]:
import os

In [3]:
ONNX_MODEL_DIR = './Flask/Models/'

FLASK_MODEL_DIR = './Flask/Models/'

TRITON_MODEL_DIR = './Triton/Models/'
TRITON_CONFIG_FILE = 'config.pbtxt'
TRITON_MODEL_FILE = 'model.plan'

In [4]:
def save_tensorrt_model(onnx_model, trt_model, precision, config):
    trt_model = trt_model + '_' + precision
    onnx_model_path = os.path.join(ONNX_MODEL_DIR, onnx_model + '.onnx')
    flask_model_path = os.path.join(FLASK_MODEL_DIR, trt_model + '.plan')

    !trtexec \
        --onnx=$onnx_model_path \
        --explicitBatch \
        --$precision \
        --saveEngine=$flask_model_path

    triton_config_path = os.path.join(TRITON_MODEL_DIR, trt_model, TRITON_CONFIG_FILE)
    os.makedirs(os.path.dirname(triton_config_path), exist_ok=True)
    with open(triton_config_path, 'w') as f:
        f.write(config.strip())

    triton_model_path = os.path.join(TRITON_MODEL_DIR, trt_model, '1', TRITON_MODEL_FILE)
    os.makedirs(os.path.dirname(triton_model_path), exist_ok=True)
    !cp $flask_model_path $triton_model_path
        
    print(flask_model_path)
    print(triton_config_path)
    print(triton_model_path)
    return

In [5]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/resnet34-trt_best.plan
[09/16/2022-07:38:55] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:38:55] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:38:55] [I] === Model Options ===
[09/16/2022-07:38:55] [I] Format: ONNX
[09/16/2022-07:38:55] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/16/2022-07:38:55] [I] Output:
[09/16/2022-07:38:55] [I] === Build Options ===
[09/16/2022-07:38:55] [I] Max batch: explicit batch
[09/16/2022-07:38:55] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:38:55] [I] minTiming: 1
[09/16/2022-07:38:55] [I] avgTiming: 8
[09/16/2022-07:38:55] [I] Precision: FP32+FP16+INT8
[09/16/2022-07:38:55] [I] LayerPrecisions: 
[09

[09/16/2022-07:39:05] [W] [TRT] Weights [name=Conv_3 + Relu_4.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:05] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:05] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:05] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:05] [W] [TRT] Weights [name=Conv_3 + Relu_4.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:05] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:05] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:05] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the wei

[09/16/2022-07:39:07] [W] [TRT] Weights [name=Conv_10 + Add_11 + Relu_12.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:07] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:07] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:07] [W] [TRT] Weights [name=Conv_13 + Relu_14.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:07] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:07] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:07] [W] [TRT] Weights [name=Conv_13 + Relu_14.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:07] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:07] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/16/2022-07:39:08] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:08] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:08] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:08] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:08] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:08] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:08] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:08] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:08] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-07:39:11] [W] [TRT] Weights [name=Conv_24 + Relu_25.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:11] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:11] [W] [TRT] Weights [name=Conv_24 + Relu_25.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:11] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the

...

[09/16/2022-07:39:24] [W] [TRT] Weights [name=Conv_72 + Add_74 + Relu_75.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:25] [W] [TRT] Weights [name=Conv_72 + Add_74 + Relu_75.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:26] [W] [TRT] Weights [name=Conv_76 + Relu_77.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:26] [W] [TRT]  - Values less than smallest positive FP16 Subnorma

[09/16/2022-07:39:28] [W] [TRT] Weights [name=Conv_78 + Add_79 + Relu_80.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:29] [W] [TRT] Weights [name=Conv_78 + Add_79 + Relu_80.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:29] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:29] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:29] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce th

[09/16/2022-07:39:31] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:31] [W] [TRT] Weights [name=Gemm_88.bias] had the following issues when converted to FP16:
[09/16/2022-07:39:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:31] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-07:39:31] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:31] [W] [TRT] Weights [name=Gemm_88.bias] had the following issues when converted to FP16:
[09/16/2022-07:39:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:31] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

./Flask/Models/resnet34-trt_best.plan
./Triton/Models/resnet34-trt_best/config.pbtxt
./Triton/Models/resnet34-trt_best/1/model.plan


In [6]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/resnet34-trt_fp16.plan
[09/16/2022-07:39:35] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:39:35] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:39:35] [I] === Model Options ===
[09/16/2022-07:39:35] [I] Format: ONNX
[09/16/2022-07:39:35] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/16/2022-07:39:35] [I] Output:
[09/16/2022-07:39:35] [I] === Build Options ===
[09/16/2022-07:39:35] [I] Max batch: explicit batch
[09/16/2022-07:39:35] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:39:35] [I] minTiming: 1
[09/16/2022-07:39:35] [I] avgTiming: 8
[09/16/2022-07:39:35] [I] Precision: FP32+FP16
[09/16/2022-07:39:35] [I] LayerPrecisions: 
[09/16/2

[09/16/2022-07:39:40] [W] [TRT] Weights [name=Conv_0 + Relu_1.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:40] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:40] [W] [TRT] Weights [name=Conv_0 + Relu_1.bias] had the following issues when converted to FP16:
[09/16/2022-07:39:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:40] [W] [TRT] Weights [name=Conv_0 + Relu_1.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:40] [W] [

[09/16/2022-07:39:42] [W] [TRT] Weights [name=Conv_5 + Add_6 + Relu_7.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:42] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:42] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:42] [W] [TRT] Weights [name=Conv_5 + Add_6 + Relu_7.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:42] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:42] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:42] [W] [TRT] Weights [name=Conv_5 + Add_6 + Relu_7.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:42] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:42] [W] [TRT] If this is not the desired behavior, please modify 

[09/16/2022-07:39:42] [W] [TRT] Weights [name=Conv_15 + Add_16 + Relu_17.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:42] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:42] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:42] [W] [TRT] Weights [name=Conv_15 + Add_16 + Relu_17.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:42] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:42] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:42] [W] [TRT] Weights [name=Conv_15 + Add_16 + Relu_17.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:42] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:42] [W] [TRT] If this is not the desired behavior, pleas

[09/16/2022-07:39:44] [W] [TRT] Weights [name=Conv_20 + Add_22 + Relu_23.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:45] [W] [TRT] Weights [name=Conv_24 + Relu_25.weight] had the following issues when converted to FP16:
[09/16/2022-07:39:45] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:39:45] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:39:45] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:39:45] [W] [TRT] Weights [name=Conv_24 + Relu_25.weight] had the following issues when converted to FP16:
[09/16/202

...

[09/16/2022-07:40:00] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-07:40:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:00] [W] [TRT] Weights [name=Gemm_88.bias] had the following issues when converted to FP16:
[09/16/2022-07:40:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:00] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-07:40:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-07:40:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:00] [W] [TRT] Weights [name=Conv_41 + Add_43 + Relu_44.weight] had the following issues when converted to FP16:
[09/16/2022-07:40:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:00] [W] [TRT] Weights [name=Conv_45 + Relu_46.weight] had the following issues when converted to FP16:
[09/16/2022-07:40:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:00] [W] [TRT] Weights [name=Conv_47 + Add_48 + Relu_49.weight] had the following issues when conv

[09/16/2022-07:40:00] [I] [TRT] Total Host Persistent Memory: 95264
[09/16/2022-07:40:00] [I] [TRT] Total Device Persistent Memory: 75776
[09/16/2022-07:40:00] [I] [TRT] Total Scratch Memory: 0
[09/16/2022-07:40:00] [I] [TRT] [MemUsageStats] Peak memory usage of TRT CPU/GPU memory allocators: CPU 45 MiB, GPU 1131 MiB
[09/16/2022-07:40:00] [I] [TRT] [BlockAssignment] Algorithm ShiftNTopDown took 1.39477ms to assign 5 blocks to 57 nodes requiring 2408456 bytes.
[09/16/2022-07:40:00] [I] [TRT] Total Activation Memory: 2408456
[09/16/2022-07:40:00] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in building engine: CPU +40, GPU +43, now: CPU 40, GPU 43 (MiB)
[09/16/2022-07:40:00] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a network created with NetworkDefinitionCreationFlag::kEXPLICIT_BATCH flag. This function will always return 1.
[09/16/2022-07:40:00] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a 

[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402502 ms - Host latency: 0.440674 ms (enqueue 0.19469 ms)
[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402649 ms - Host latency: 0.440723 ms (enqueue 0.195569 ms)
[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402612 ms - Host latency: 0.440637 ms (enqueue 0.195447 ms)
[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402612 ms - Host latency: 0.440833 ms (enqueue 0.194104 ms)
[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402527 ms - Host latency: 0.440613 ms (enqueue 0.194238 ms)
[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402832 ms - Host latency: 0.441125 ms (enqueue 0.194397 ms)
[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402454 ms - Host latency: 0.441577 ms (enqueue 0.19845 ms)
[09/16/2022-07:40:04] [I] Average on 10 runs - GPU latency: 0.402844 ms - Host latency: 0.440967 ms (enqueue 0.195239 ms)
[09/16/2022-07:40:04] [I] 

./Flask/Models/resnet34-trt_fp16.plan
./Triton/Models/resnet34-trt_fp16/config.pbtxt
./Triton/Models/resnet34-trt_fp16/1/model.plan


In [7]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/resnet34-trt_int8.plan
[09/16/2022-07:40:04] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:40:04] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:40:04] [I] === Model Options ===
[09/16/2022-07:40:04] [I] Format: ONNX
[09/16/2022-07:40:04] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/16/2022-07:40:04] [I] Output:
[09/16/2022-07:40:04] [I] === Build Options ===
[09/16/2022-07:40:04] [I] Max batch: explicit batch
[09/16/2022-07:40:04] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:40:04] [I] minTiming: 1
[09/16/2022-07:40:04] [I] avgTiming: 8
[09/16/2022-07:40:04] [I] Precision: FP32+INT8
[09/16/2022-07:40:04] [I] LayerPrecisions: 
[09/16/2

./Flask/Models/resnet34-trt_int8.plan
./Triton/Models/resnet34-trt_int8/config.pbtxt
./Triton/Models/resnet34-trt_int8/1/model.plan


In [8]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/mobilenet_v2-trt_best.plan
[09/16/2022-07:40:26] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:40:26] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:40:26] [I] === Model Options ===
[09/16/2022-07:40:26] [I] Format: ONNX
[09/16/2022-07:40:26] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/16/2022-07:40:26] [I] Output:
[09/16/2022-07:40:26] [I] === Build Options ===
[09/16/2022-07:40:26] [I] Max batch: explicit batch
[09/16/2022-07:40:26] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:40:26] [I] minTiming: 1
[09/16/2022-07:40:26] [I] avgTiming: 8
[09/16/2022-07:40:26] [I] Precision: FP32+FP16+INT8
[09/16/2022-07:40:26] [I] LayerPrec

[09/16/2022-07:40:47] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/16/2022-07:40:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:47] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/16/2022-07:40:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:51] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/16/2022-07:40:51] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:51] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/16/2022-07:40:55] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-07:40:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:55] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-07:40:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:40:55] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-07:40:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:40:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduc

[09/16/2022-07:41:00] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-07:41:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:00] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-07:41:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:00] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-07:41:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:00] [W] [TRT] If this is not the desired behavior, please modify the

[09/16/2022-07:41:03] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:03] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:03] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

...

[09/16/2022-07:41:43] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:43] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:43] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-07:41:44] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-07:41:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:44] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-07:41:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:45] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-07:41:45] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:45] [W] [TRT] If this is not the desired behavior, please modify the

[09/16/2022-07:41:47] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:47] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:41:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:47] [W] [TRT] Weights [name=Gemm_99.bias] had the following issues when converted to FP16:
[09/16/2022-07:41:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:41:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:41:47] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-07:41:47] [W] [TRT]  - Subnormal FP16 v

[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.199219 ms - Host latency: 0.244385 ms (enqueue 0.147852 ms)
[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.199316 ms - Host latency: 0.244775 ms (enqueue 0.147803 ms)
[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.199463 ms - Host latency: 0.244775 ms (enqueue 0.1479 ms)
[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.199463 ms - Host latency: 0.244727 ms (enqueue 0.148413 ms)
[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.199536 ms - Host latency: 0.244897 ms (enqueue 0.147656 ms)
[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.200098 ms - Host latency: 0.24563 ms (enqueue 0.148096 ms)
[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.199341 ms - Host latency: 0.245117 ms (enqueue 0.148389 ms)
[09/16/2022-07:41:51] [I] Average on 10 runs - GPU latency: 0.199536 ms - Host latency: 0.245044 ms (enqueue 0.148193 ms)
[09/16/2022-07:41:51] [I] A

./Flask/Models/mobilenet_v2-trt_best.plan
./Triton/Models/mobilenet_v2-trt_best/config.pbtxt
./Triton/Models/mobilenet_v2-trt_best/1/model.plan


In [9]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/mobilenet_v2-trt_fp16.plan
[09/16/2022-07:41:51] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:41:51] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:41:51] [I] === Model Options ===
[09/16/2022-07:41:51] [I] Format: ONNX
[09/16/2022-07:41:51] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/16/2022-07:41:51] [I] Output:
[09/16/2022-07:41:51] [I] === Build Options ===
[09/16/2022-07:41:51] [I] Max batch: explicit batch
[09/16/2022-07:41:51] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:41:51] [I] minTiming: 1
[09/16/2022-07:41:51] [I] avgTiming: 8
[09/16/2022-07:41:51] [I] Precision: FP32+FP16
[09/16/2022-07:41:51] [I] LayerPrecision

[09/16/2022-07:42:01] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:01] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:01] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:04] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:04] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:04] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:04] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/16/2022-07:42:07] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:07] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:07] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:07] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:07] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:07] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:07] [W] [TRT] Weights [name=Conv_10 + PWN(Clip_11).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:07] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:07] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regular

[09/16/2022-07:42:11] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:11] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:11] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:11] [W] [TRT] If this is not the desired behavior, please modify the

[09/16/2022-07:42:14] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:14] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:14] [W] [TRT] Weights [name=Conv_21 + PWN(Clip_22).weight] had the following issues when converted to FP16:
[09/16/2022-07:42:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regul

...

[09/16/2022-07:42:50] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:50] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:50] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:42:50] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:50] [W] [TRT] Weights [name=Gemm_99.bias] had the following issues when converted to FP16:
[09/16/2022-07:42:50] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:50] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:50] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:50] [W] [TRT]  - Subnormal FP16 v

[09/16/2022-07:42:50] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:50] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:50] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:42:50] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:50] [W] [TRT] Weights [name=Gemm_99.bias] had the following issues when converted to FP16:
[09/16/2022-07:42:50] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:42:50] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:42:50] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-07:42:50] [W] [TRT]  - Subnormal FP16 v

[09/16/2022-07:42:51] [I] Engine built in 59.4305 sec.
[09/16/2022-07:42:51] [I] [TRT] [MemUsageChange] Init CUDA: CPU +0, GPU +0, now: CPU 1312, GPU 972 (MiB)
[09/16/2022-07:42:51] [I] [TRT] Loaded engine size: 9 MiB
[09/16/2022-07:42:51] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in engine deserialization: CPU +0, GPU +9, now: CPU 0, GPU 9 (MiB)
[09/16/2022-07:42:51] [I] Engine deserialized in 0.00479625 sec.
[09/16/2022-07:42:51] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in IExecutionContext creation: CPU +0, GPU +3, now: CPU 0, GPU 12 (MiB)
[09/16/2022-07:42:51] [I] Using random values for input input_0
[09/16/2022-07:42:51] [I] Created input binding for input_0 with dimensions 1x3x224x224
[09/16/2022-07:42:51] [I] Using random values for output output_0
[09/16/2022-07:42:51] [I] Created output binding for output_0 with dimensions 1x1000
[09/16/2022-07:42:51] [I] Starting inference
[09/16/2022-07:42:54] [I] Warmup completed 694 queries over 200 ms
[09/16/20

[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.272607 ms - Host latency: 0.306409 ms (enqueue 0.150269 ms)
[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.273132 ms - Host latency: 0.306714 ms (enqueue 0.151953 ms)
[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.272083 ms - Host latency: 0.305774 ms (enqueue 0.149768 ms)
[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.2729 ms - Host latency: 0.306641 ms (enqueue 0.150537 ms)
[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.332617 ms - Host latency: 0.365894 ms (enqueue 0.151538 ms)
[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.272888 ms - Host latency: 0.306396 ms (enqueue 0.149646 ms)
[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.272278 ms - Host latency: 0.305481 ms (enqueue 0.152368 ms)
[09/16/2022-07:42:54] [I] Average on 10 runs - GPU latency: 0.273071 ms - Host latency: 0.30658 ms (enqueue 0.149561 ms)
[09/16/2022-07:42:54] [I] A

./Flask/Models/mobilenet_v2-trt_fp16.plan
./Triton/Models/mobilenet_v2-trt_fp16/config.pbtxt
./Triton/Models/mobilenet_v2-trt_fp16/1/model.plan


In [10]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/mobilenet_v2-trt_int8.plan
[09/16/2022-07:42:55] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:42:55] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:42:55] [I] === Model Options ===
[09/16/2022-07:42:55] [I] Format: ONNX
[09/16/2022-07:42:55] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/16/2022-07:42:55] [I] Output:
[09/16/2022-07:42:55] [I] === Build Options ===
[09/16/2022-07:42:55] [I] Max batch: explicit batch
[09/16/2022-07:42:55] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:42:55] [I] minTiming: 1
[09/16/2022-07:42:55] [I] avgTiming: 8
[09/16/2022-07:42:55] [I] Precision: FP32+INT8
[09/16/2022-07:42:55] [I] LayerPrecision

[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.199878 ms - Host latency: 0.236633 ms (enqueue 0.147577 ms)
[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.19906 ms - Host latency: 0.235132 ms (enqueue 0.147711 ms)
[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.246381 ms - Host latency: 0.283044 ms (enqueue 0.147943 ms)
[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.217279 ms - Host latency: 0.253949 ms (enqueue 0.147241 ms)
[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.198859 ms - Host latency: 0.23493 ms (enqueue 0.147345 ms)
[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.199176 ms - Host latency: 0.235156 ms (enqueue 0.147021 ms)
[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.199176 ms - Host latency: 0.235211 ms (enqueue 0.146796 ms)
[09/16/2022-07:43:47] [I] Average on 10 runs - GPU latency: 0.199683 ms - Host latency: 0.23573 ms (enqueue 0.147681 ms)
[09/16/2022-07:43:47] [I] A

./Flask/Models/mobilenet_v2-trt_int8.plan
./Triton/Models/mobilenet_v2-trt_int8/config.pbtxt
./Triton/Models/mobilenet_v2-trt_int8/1/model.plan


In [11]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/efficientnet_b0-trt_best.plan
[09/16/2022-07:43:47] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:43:47] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:43:47] [I] === Model Options ===
[09/16/2022-07:43:47] [I] Format: ONNX
[09/16/2022-07:43:47] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/16/2022-07:43:47] [I] Output:
[09/16/2022-07:43:47] [I] === Build Options ===
[09/16/2022-07:43:47] [I] Max batch: explicit batch
[09/16/2022-07:43:47] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:43:47] [I] minTiming: 1
[09/16/2022-07:43:47] [I] avgTiming: 8
[09/16/2022-07:43:47] [I] Precision: FP32+FP16+INT8
[09/16/2022-07:43:47] [I] 

[09/16/2022-07:45:46] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-07:45:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:45:46] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:45:46] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:45:46] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-07:45:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:45:46] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:45:46] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with reg

[09/16/2022-07:45:49] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/16/2022-07:45:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:45:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:45:49] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/16/2022-07:45:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:45:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:45:50] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/16/2022-07:45:50] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:45:50] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-07:46:01] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:01] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:01] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:01] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:01] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:01] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:01] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:01] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:01] [W] [TRT] If this is not the desired behavior, please modify the weights or retrai

[09/16/2022-07:46:02] [W] [TRT] Weights [name=Conv_43 + PWN(PWN(Sigmoid_44), Mul_45).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:02] [W] [TRT] Weights [name=Conv_43 + PWN(PWN(Sigmoid_44), Mul_45).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:02] [W] [TRT] Weights [name=Conv_46 + PWN(PWN(Sigmoid_47), Mul_48).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:02] [W] [TRT] If thi

...

[09/16/2022-07:46:25] [W] [TRT] Weights [name=Conv_222 + PWN(PWN(Sigmoid_223), Mul_224).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:25] [W] [TRT] Weights [name=Conv_222 + PWN(PWN(Sigmoid_223), Mul_224).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:25] [W] [TRT] Weights [name=Conv_222 + PWN(PWN(Sigmoid_223), Mul_224).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:25] [W] [TR

[09/16/2022-07:46:25] [W] [TRT] Weights [name=Conv_232.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:25] [W] [TRT] Weights [name=Conv_232.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:25] [W] [TRT] Weights [name=Conv_232.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to

[09/16/2022-07:46:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:26] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:26] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-07:46:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:26] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234

[09/16/2022-07:46:27] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:27] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:27] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:27] [W] [TRT] Weights [name=Gemm_238.bias] had the following issues when converted to FP16:
[09/16/2022-07:46:27] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:27] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:46:27] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-07:46:27] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:46:27] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to r

./Flask/Models/efficientnet_b0-trt_best.plan
./Triton/Models/efficientnet_b0-trt_best/config.pbtxt
./Triton/Models/efficientnet_b0-trt_best/1/model.plan


In [12]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/efficientnet_b0-trt_fp16.plan
[09/16/2022-07:46:32] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:46:32] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:46:32] [I] === Model Options ===
[09/16/2022-07:46:32] [I] Format: ONNX
[09/16/2022-07:46:32] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/16/2022-07:46:32] [I] Output:
[09/16/2022-07:46:32] [I] === Build Options ===
[09/16/2022-07:46:32] [I] Max batch: explicit batch
[09/16/2022-07:46:32] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:46:32] [I] minTiming: 1
[09/16/2022-07:46:32] [I] avgTiming: 8
[09/16/2022-07:46:32] [I] Precision: FP32+FP16
[09/16/2022-07:46:32] [I] Layer

[09/16/2022-07:48:26] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:26] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:48:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:48:26] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:26] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:48:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with reg

[09/16/2022-07:48:33] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:33] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:48:33] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:33] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:48:33] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:33] [W] [TRT] If thi

[09/16/2022-07:48:43] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-07:48:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:48:43] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-07:48:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:48:44] [W] [TRT] Weights [name=Conv_43 + PWN(PWN(Sigmoid_44), Mul_45).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:44] [W] [TRT] If this is not the desired behavior, please modify

[09/16/2022-07:48:49] [W] [TRT] Weights [name=Conv_57 + PWN(PWN(Sigmoid_58), Mul_59).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:48:49] [W] [TRT] Weights [name=Conv_57 + PWN(PWN(Sigmoid_58), Mul_59).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:48:49] [W] [TRT] Weights [name=Conv_57 + PWN(PWN(Sigmoid_58), Mul_59).weight] had the following issues when converted to FP16:
[09/16/2022-07:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:48:49] [W] [TRT] If thi

...

[09/16/2022-07:50:00] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-07:50:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:50:00] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-07:50:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:00] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:50:01] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-07:50:01] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:01] [W] [TRT] If this is not the desired beh

[09/16/2022-07:50:01] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-07:50:01] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:01] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:50:01] [W] [TRT] Weights [name=Gemm_238.bias] had the following issues when converted to FP16:
[09/16/2022-07:50:01] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:01] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:50:02] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-07:50:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to r

[09/16/2022-07:50:02] [W] [TRT] Weights [name=Conv_140.weight] had the following issues when converted to FP16:
[09/16/2022-07:50:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:50:02] [W] [TRT] Weights [name=Conv_143 + Add_144.weight] had the following issues when converted to FP16:
[09/16/2022-07:50:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:50:02] [W] [TRT] Weights [name=Conv_145 + PWN(PWN(Sigmoid_146), Mul_147).weight] had the following issues when converted to FP16:
[09/16/2022-07:50:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:50:02] [W] [TRT]  - Values less than smallest positive FP16 Subnormal 

[09/16/2022-07:50:02] [I] [TRT] Total Host Persistent Memory: 207104
[09/16/2022-07:50:02] [I] [TRT] Total Device Persistent Memory: 0
[09/16/2022-07:50:02] [I] [TRT] Total Scratch Memory: 0
[09/16/2022-07:50:02] [I] [TRT] [MemUsageStats] Peak memory usage of TRT CPU/GPU memory allocators: CPU 12 MiB, GPU 2826 MiB
[09/16/2022-07:50:02] [I] [TRT] [BlockAssignment] Algorithm ShiftNTopDown took 25.7379ms to assign 6 blocks to 198 nodes requiring 3807236 bytes.
[09/16/2022-07:50:02] [I] [TRT] Total Activation Memory: 3807236
[09/16/2022-07:50:02] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in building engine: CPU +8, GPU +13, now: CPU 8, GPU 13 (MiB)
[09/16/2022-07:50:02] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a network created with NetworkDefinitionCreationFlag::kEXPLICIT_BATCH flag. This function will always return 1.
[09/16/2022-07:50:02] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a netw

./Flask/Models/efficientnet_b0-trt_fp16.plan
./Triton/Models/efficientnet_b0-trt_fp16/config.pbtxt
./Triton/Models/efficientnet_b0-trt_fp16/1/model.plan


In [13]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/efficientnet_b0-trt_int8.plan
[09/16/2022-07:50:06] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:50:06] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:50:06] [I] === Model Options ===
[09/16/2022-07:50:06] [I] Format: ONNX
[09/16/2022-07:50:06] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/16/2022-07:50:06] [I] Output:
[09/16/2022-07:50:06] [I] === Build Options ===
[09/16/2022-07:50:06] [I] Max batch: explicit batch
[09/16/2022-07:50:06] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:50:06] [I] minTiming: 1
[09/16/2022-07:50:06] [I] avgTiming: 8
[09/16/2022-07:50:06] [I] Precision: FP32+INT8
[09/16/2022-07:50:06] [I] Layer

./Flask/Models/efficientnet_b0-trt_int8.plan
./Triton/Models/efficientnet_b0-trt_int8/config.pbtxt
./Triton/Models/efficientnet_b0-trt_int8/1/model.plan


In [14]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/efficientnet_b7-trt_best.plan
[09/16/2022-07:51:29] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:51:29] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:51:29] [I] === Model Options ===
[09/16/2022-07:51:29] [I] Format: ONNX
[09/16/2022-07:51:29] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/16/2022-07:51:29] [I] Output:
[09/16/2022-07:51:29] [I] === Build Options ===
[09/16/2022-07:51:29] [I] Max batch: explicit batch
[09/16/2022-07:51:29] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:51:29] [I] minTiming: 1
[09/16/2022-07:51:29] [I] avgTiming: 8
[09/16/2022-07:51:29] [I] Precision: FP32+FP16+INT8
[09/16/2022-07:51:29] [I] 

[09/16/2022-07:53:08] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/16/2022-07:53:08] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:08] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:53:08] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/16/2022-07:53:08] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:08] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:53:08] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/16/2022-07:53:08] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:08] [W] [TRT] If this is not 

[09/16/2022-07:53:10] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-07:53:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:53:10] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/16/2022-07:53:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:53:10] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-07:53:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-07:53:10] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-07:53:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:53:10] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/16/2022-07:53:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:53:10] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-07:53:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:53:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-07:54:14] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-07:54:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:54:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:54:14] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-07:54:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:54:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:54:14] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-07:54:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:54:14] [W] [TRT] If thi

...

[09/16/2022-07:55:28] [W] [TRT] Weights [name=Conv_804.weight] had the following issues when converted to FP16:
[09/16/2022-07:55:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:55:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:55:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:55:28] [W] [TRT] Weights [name=Conv_804.bias] had the following issues when converted to FP16:
[09/16/2022-07:55:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:55:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:55:28] [W] [TRT] Weights [name=Conv_804.weight] had the following issues when converted to FP16:
[09/16/2022-07:55:28] [W] [TRT]  - Subnormal FP1

[09/16/2022-07:55:28] [W] [TRT] Weights [name=Conv_807 + Add_808.weight] had the following issues when converted to FP16:
[09/16/2022-07:55:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:55:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:55:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:55:28] [W] [TRT] Weights [name=Conv_807 + Add_808.weight] had the following issues when converted to FP16:
[09/16/2022-07:55:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:55:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:55:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of t

[09/16/2022-07:55:28] [W] [TRT] Weights [name=Conv_809 + PWN(PWN(Sigmoid_810), Mul_811).weight] had the following issues when converted to FP16:
[09/16/2022-07:55:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:55:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:55:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:55:28] [W] [TRT] Weights [name=Conv_809 + PWN(PWN(Sigmoid_810), Mul_811).weight] had the following issues when converted to FP16:
[09/16/2022-07:55:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:55:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-07:55:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain wi

[09/16/2022-07:55:30] [I] [TRT] Detected 1 inputs and 1 output network tensors.
[09/16/2022-07:55:30] [W] [TRT] Weights [name=Conv_0 + PWN(PWN(Sigmoid_1), Mul_2).weight] had the following issues when converted to FP16:
[09/16/2022-07:55:30] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:55:30] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:55:31] [I] [TRT] Total Host Persistent Memory: 510016
[09/16/2022-07:55:31] [I] [TRT] Total Device Persistent Memory: 0
[09/16/2022-07:55:31] [I] [TRT] Total Scratch Memory: 22536
[09/16/2022-07:55:31] [I] [TRT] [MemUsageStats] Peak memory usage of TRT CPU/GPU memory allocators: CPU 66 MiB, GPU 20460 MiB
[09/16/2022-07:55:31] [I] [TRT] [BlockAssignment] Algorithm ShiftNTopDown took 116.692ms to assign 5 blocks to 392 nodes requiring 28081152 bytes.
[09/16/2022-07:55:31] [I] [TRT] Total Activation Memory: 28081152
[09/16/2022-0

./Flask/Models/efficientnet_b7-trt_best.plan
./Triton/Models/efficientnet_b7-trt_best/config.pbtxt
./Triton/Models/efficientnet_b7-trt_best/1/model.plan


In [15]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/efficientnet_b7-trt_fp16.plan
[09/16/2022-07:55:36] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-07:55:36] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-07:55:36] [I] === Model Options ===
[09/16/2022-07:55:36] [I] Format: ONNX
[09/16/2022-07:55:36] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/16/2022-07:55:36] [I] Output:
[09/16/2022-07:55:36] [I] === Build Options ===
[09/16/2022-07:55:36] [I] Max batch: explicit batch
[09/16/2022-07:55:36] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-07:55:36] [I] minTiming: 1
[09/16/2022-07:55:36] [I] avgTiming: 8
[09/16/2022-07:55:36] [I] Precision: FP32+FP16
[09/16/2022-07:55:36] [I] Layer

[09/16/2022-07:56:08] [W] [TRT] Weights [name=Conv_0.weight] had the following issues when converted to FP16:
[09/16/2022-07:56:08] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:56:08] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:56:47] [W] [TRT] Weights [name=Conv_3.weight] had the following issues when converted to FP16:
[09/16/2022-07:56:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:56:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:56:48] [W] [TRT] Weights [name=Conv_3.weight] had the following issues when converted to FP16:
[09/16/2022-07:56:48] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:56:48] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduc

[09/16/2022-07:56:57] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-07:56:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:56:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:56:57] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/16/2022-07:56:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:56:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:56:57] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-07:56:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:56:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-07:57:38] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/16/2022-07:57:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:57:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:57:38] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/16/2022-07:57:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:57:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:57:38] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/16/2022-07:57:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:57:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-07:57:44] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-07:57:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:57:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:57:44] [W] [TRT] Weights [name=Conv_21.bias] had the following issues when converted to FP16:
[09/16/2022-07:57:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:57:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-07:57:44] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-07:57:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-07:57:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

...

[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_682 + PWN(PWN(Sigmoid_683), Mul_684).weight] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_682 + PWN(PWN(Sigmoid_683), Mul_684).bias] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_685.weight] had the following issues when c

[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_723.weight] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_727 + PWN(PWN(Sigmoid_728), Mul_729).weight] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_727 + PWN(PWN(Sigmoid_728), Mul_729).bias] had the following issues when c

[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_764 + PWN(PWN(Sigmoid_765), Mul_766).weight] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_771 + PWN(PWN(Sigmoid_772), Mul_773).weight] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value d

[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_807 + Add_808.weight] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:00:57] [W] [TRT] Weights [name=Conv_809 + PWN(PWN(Sigmoid_810), Mul_811).weight] had the following issues when converted to FP16:
[09/16/2022-08:00:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:00:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:00:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

./Flask/Models/efficientnet_b7-trt_fp16.plan
./Triton/Models/efficientnet_b7-trt_fp16/config.pbtxt
./Triton/Models/efficientnet_b7-trt_fp16/1/model.plan


In [16]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 32
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/efficientnet_b7-trt_int8.plan
[09/16/2022-08:01:02] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:01:02] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:01:02] [I] === Model Options ===
[09/16/2022-08:01:02] [I] Format: ONNX
[09/16/2022-08:01:02] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/16/2022-08:01:02] [I] Output:
[09/16/2022-08:01:02] [I] === Build Options ===
[09/16/2022-08:01:02] [I] Max batch: explicit batch
[09/16/2022-08:01:02] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:01:02] [I] minTiming: 1
[09/16/2022-08:01:02] [I] avgTiming: 8
[09/16/2022-08:01:02] [I] Precision: FP32+INT8
[09/16/2022-08:01:02] [I] Layer

./Flask/Models/efficientnet_b7-trt_int8.plan
./Triton/Models/efficientnet_b7-trt_int8/config.pbtxt
./Triton/Models/efficientnet_b7-trt_int8/1/model.plan
